In [8]:
import sys
from time import time
from tqdm import tqdm
import random 
import json
sys.path.insert(0, '../KGWatermark')
from extended_watermark_processor import WatermarkLogitsProcessor
from extended_watermark_processor import WatermarkDetector
from transformers import AutoTokenizer, AutoModelForCausalLM
from transformers import LogitsProcessorList
from transformers import GenerationConfig
from datasets import load_dataset
import torch
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    HfArgumentParser,
    AutoTokenizer,
    TrainingArguments,
    Trainer,
    GenerationConfig
)
import os
import re
import copy
import json
from extended_watermark_processor import WatermarkDetector
import time
import requests
from tqdm import tqdm
from random import shuffle
from pprint import pprint
from langchain_openai import ChatOpenAI
from langchain.prompts import ChatPromptTemplate
from requests.exceptions import ConnectionError
import numpy as np
from GET_API_KEY import GET_OPENAI_API_KEY()
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cuda


In [17]:
dataset = load_dataset("allenai/c4", "realnewslike")

Resolving data files:   0%|          | 0/1024 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/512 [00:00<?, ?it/s]

Loading dataset shards:   0%|          | 0/76 [00:00<?, ?it/s]

In [24]:
tokenizer = AutoTokenizer.from_pretrained("facebook/opt-6.7b", device_map = 'auto')
compute_dtype = getattr(torch, "float16")
bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type='nf4',
        bnb_4bit_compute_dtype=compute_dtype,
        bnb_4bit_use_double_quant=False,
    )
model = AutoModelForCausalLM.from_pretrained("facebook/opt-6.7b",quantization_config = bnb_config, device_map = 'auto')
# del model
# torch.cuda.empty_cache()

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

/usr/local/miniconda3/lib/python3.11/site-packages/torch/_utils.py:776: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()


In [62]:
# input_text = '''Repeat the following content: {}. Repitition:'''.format("(Malaclemys terrapin) is a species of turtle native to the brackish coastal tidal")
# print(input_text)
# input_text = '''Repeat the following content: The diamondback terrapin or simply terrapin (Malaclemys terrapin) is a species of turtle native to the brackish coastal tidal marshes of the Northeastern and southern United States, and in Bermuda.[6] It belongs to the monotypic genus Malaclemys. It has one of the largest ranges of all turtles in North America, stretching as far south as the Florida Keys and as far north as Cape Cod.[7] The name 'terrapin' is derived from the Algonquian word torope.[8] It applies to Malaclemys terrapin in both British English and American English. The name originally was used by early European settlers in North America to describe these brackish-water turtles that inhabited neither freshwater habitats nor the sea. It retains this primary meaning in American English.[8] In British English, however, other semi-aquatic turtle species, such as the red-eared slider, might also be called terrapins. The common name refers to the diamond pattern on top of its shell (carapace), but the overall pattern and coloration vary greatly. The shell is usually wider at the back than in the front, and from above it appears wedge-shaped. The shell coloring can vary from brown to grey, and its body color can be grey, brown, yellow, or white. All have a unique pattern of wiggly, black markings or spots on their body and head. The diamondback terrapin has large webbed feet.[9] The species is'''

truncated_dataset = []
threshold = 70

for row in dataset['validation']:
    truncated_dataset.append(row['text'][:threshold])

print("Start Tokenization...")
tokenized_tensors = list(map(lambda s: tokenizer(s, return_tensors='pt'), dataset['validation']['text']))
print("End Tokenization...")

truncated_tokenized_tensors = []
decoded_text_inputs = []
for item in tqdm(tokenized_tensors, desc="Processing"):
    truncated_tokenized_tensors.append({'input_ids':item['input_ids'][:, :threshold].to(device), 
                                        'attention_mask': item['attention_mask'][:,:threshold].to(device)})

for item in tqdm(truncated_tokenized_tensors):
    # Assuming 'input_ids' are on the CPU for decoding
    input_ids = item['input_ids'][0].cpu().numpy()
    decoded_text_input = tokenizer.decode(input_ids, skip_special_tokens=True)
    decoded_text_inputs.append(decoded_text_input)

assert(len(decoded_text_inputs) == len(truncated_tokenized_tensors)), "There's something wrong with decoding."


Start Tokenization...
End Tokenization...


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 13863/13863 [00:00<00:00, 21568.56it/s]


In [28]:
watermark_processor = WatermarkLogitsProcessor(vocab=list(tokenizer.get_vocab().values()),
                                               gamma=0.25,
                                               delta=2.0,
                                               seeding_scheme="selfhash") #equivalent to `ff-anchored_minhash_prf-4-True-15485863`
# Note:
# You can turn off self-hashing by setting the seeding scheme to `minhash`.

output_text_list = []
output_text_normal_list = []
epoch = 1000

print(f"Mode's loaded on {model.device}")
print(f"Data's loaded on {truncated_tokenized_tensors[0]['input_ids'].device}")

Mode's loaded on cuda:0
Data's loaded on cuda:0


In [29]:
generation_config = GenerationConfig(
        max_new_tokens=80,        
        # do_sample = True,
        num_beams = 4,
        early_stopping = True,
        # temperature = 0.35,
        no_repeat_ngram_size = 4,
        # top_p=0.92
    )
epoch = 2000
for item in tqdm(truncated_tokenized_tensors[:epoch]):
    # start_time = time()

    
    output_tokens = model.generate(**item,
                                   logits_processor=LogitsProcessorList([watermark_processor]),
                                   generation_config = generation_config
                                  )
    output_tokens_normal = model.generate(**item,
                                   generation_config = generation_config
                                  )
    # if decoder only model, then we need to isolate the
    # newly generated tokens as only those are watermarked, the input/prompt is not
    output_tokens = output_tokens[:,item["input_ids"].shape[-1]:]
    output_tokens_normal = output_tokens_normal[:,item["input_ids"].shape[-1]:]
    
    output_text = tokenizer.batch_decode(output_tokens, skip_special_tokens=True)[0]
    output_text_normal = tokenizer.batch_decode(output_tokens_normal, skip_special_tokens=True)[0]

    output_text_list.append(output_text)
    output_text_normal_list.append(output_text_normal)

    break
    
    # end_time = time()
    # print(end_time - start_time)

  0%|                                                                                                                                                                          | 0/2000 [00:36<?, ?it/s]


In [39]:
# output_text_list = load_json_file("output_texts.json")
# len(output_text_list)
# output_text_normal_list = load_json_file("output_normal_texts.json")
# len(output_normal_text_list)
# output_text_normal_list

{'0': "k, N.Y., said the cluster, which is based on the company's eServer 325 system, is designed to run Linux and Microsoft Corp.'s Windows Server 2003 operating system.\nThe cluster, which will be available in the second half of this year, is based on AMDs Opteron 64-bit processor, which is designed for high-performance computing, IBM said.\n",
 '1': ' 58,19,00,000 (Rs 58.19 billion), according to a report of the Comptroller and Auditor General (CAG) tabled in Parliament on Wednesday.\n\nThe CAG report said that the revenue earned by the public broadcaster during the Games was lower than the budgeted amount of Rs 1,000 crore (Rs 10 billion).\n\nThe report also said that the',
 '2': ' limited to, public relations, advertising, public affairs, public information, public affairs and marketing.\nMarketing professionals are also employed by non-profit organizations, such as the American Red Cross, the American Cancer Society, the American Heart Association, the American Lung Association, 

In [34]:
print("="*100)
print("Demo Output")
print(f"The watermarked text is: \n {decoded_text_inputs[0]}||{output_text_list[0]}")
print("*"*100)
print(f"The unwatermarked text is: \n {decoded_text_inputs[0]}||{output_text_normal_list[0]}")
print("="*100)

KeyError: 0

In [63]:
if type(output_text_list) == list and type(output_text_normal_list) == list:
    output_text_list = {str(i): text for i, text in enumerate(output_text_list)}
    output_text_normal_list = {str(i): text for i, text in enumerate(output_text_normal_list)}
    decoded_text_inputs = {str(i): text for i, text in enumerate(decoded_text_inputs)}
filename = 'output_texts.json'
filename_normal = 'output_normal_texts.json'
filename_prompt = 'prompt_list.json'
with open(filename, 'w') as f:
    json.dump(output_text_list, f, indent=4)
with open(filename_normal, 'w') as f:
    json.dump(output_text_normal_list, f, indent=4)
with open(filename_prompt, 'w') as f:
    json.dump(decoded_text_inputs, f, indent=4)
    

print(f"Data has been written to {filename}.")
print(f"Data has been written to {filename_normal}.")
print(f"Data has been written to {filename_prompt}")

Data has been written to output_texts.json.
Data has been written to output_normal_texts.json.
Data has been written to prompt_list.json


In [64]:
watermark_detector = WatermarkDetector(vocab=list(tokenizer.get_vocab().values()),
                                        gamma=0.25, # should match original setting
                                        seeding_scheme="selfhash", # should match original setting
                                        device=model.device, # must match the original rng device type
                                        tokenizer=tokenizer,
                                        z_threshold=4.0,
                                        normalizers=[],
                                        ignore_repeated_ngrams=True)

watermarked_score_dict = watermark_detector.detect(output_text_list['0']) # or any other text of interest to analyze
normal_score_dict = watermark_detector.detect(output_text_normal_list['0'])

In [65]:
print("Watermark Decoding Demo".center(100,'='))
print(f"Watermark's result: f{watermarked_score_dict}")
print(f"Unwatermarked's result: f{normal_score_dict}")

======================================Watermark Decoding Demo=======================================
Watermark's result: f{'num_tokens_scored': 77, 'num_green_tokens': 55, 'green_fraction': 0.7142857142857143, 'z_score': 9.408709237924697, 'p_value': 2.5113338670768307e-21, 'z_score_at_T': tensor([-0.5774, -0.8165, -1.0000, -1.1547, -1.2910, -1.4142, -0.6547,  0.0000,
        -0.1925,  0.3651,  0.1741,  0.6667,  0.4804,  0.9258,  1.3416,  1.7321,
         1.5403,  1.3608,  1.7219,  1.5492,  1.8898,  2.2156,  2.5281,  2.8284,
         2.6558,  2.9439,  3.2222,  3.4915,  3.7524,  4.0056,  4.2515,  4.0825,
         3.9196,  4.1586,  4.0012,  4.2339,  4.4610,  4.6829,  4.5301,  4.7469,
         4.5985,  4.4544,  4.6664,  4.5260,  4.7336,  4.9373,  5.1371,  5.3333,
         5.5261,  5.7155,  5.9017,  6.0849,  6.2651,  6.4425,  6.6172,  6.7893,
         6.9589,  6.8229,  6.9903,  7.1554,  7.3183,  7.4790,  7.3467,  7.5056,
         7.6624,  7.8174,  7.9704,  8.1216,  8.2711,  8.4188,  8.5649

In [67]:
# Data backup for following testings
backoutput_list = copy.deepcopy(output_text_list)
backoutput_list_normal = copy.deepcopy(output_text_normal_list)

In [68]:
def load_json_file(file_path):
    with open(file_path,'r',encoding='utf-8') as f:
        file = json.load(f)
        f.close()
    return file

def save_json_file(file, file_path):
    with open(file_path,'w',encoding='utf-8') as f:
        json.dump(file, f, indent=4, ensure_ascii=False)
        f.close()

In [9]:
random_seed = 127
epoch = 1000
random.seed(random_seed)


rank_prompt_string = """Please act as an impartial judge and evaluate the quality of the text completions provided by two largelanguage models to the prompt displayed below.
Assess each response according to the criteria outlined, using a 1-5 Likert scale. 
After scoring each criterion, provide a summary for each response, including examples that influenced your scoring. 
Additionally, ensure that the order in which the responses are presented does not affect your decision.
Criteria:
1. Relevance to the prompt
2. Depth of detail
3. Clarity of writing
4. Coherence and logical flow
5. Originality and insight
6. Use of specific examples
7. Accuracy of information
Start with a brief statement about which response you think is superior. 
Then, for each response and criterion, provide a score, followed by a brief justification for that score. 
At the very end of your response, declare your verdict by choosing one of the choices below, strictly following the given format:
"[[A]]: [list of scores]" if assistant A is better,
"[[B]]: [list of scores]" if assistant B is better, or
"[[C]]" for a tie.
The overall format of your output should take JSON form. For examples: {{{{"LLM A’s Answer": XXX, "LLM B's Answer": XXX, "Summary": XXX, "Verdict"： XXX}}}}
[Prompt]
{prompt}
[LLM A’s Answer]
{answer_a}
[LLM B’s Answer]
{answer_b}
"""
simple_prompt_string = """Please act as an impartial judge and evaluate the quality of the text completions provided by two large language models to the prompt displayed below. 
You should choose the LLM that completes the prompt better. Begin your evaluation by comparing the two responses and provide a short explanation. 
Avoid any position biases and ensure that the order in which the responses were presented does not influence your decision. 
Do not allow the length of the responses to influence your evaluation. Be as objective as possible.
After providing your explanation, output your final verdict by strictly following this format: "[[A]]" if assistant A is better, "[[B]]" if assistant B is better, and "[[C]]" for a tie.

[Prompt]
{prompt}

[LLM A’s Answer]
{answer_a}

[LLM B’s Answer]
{answer_b}
"""

# np.save('unwatermarked.npy', np.array(unwatermarked))
unwatermarked = list(np.load('unwatermarked.npy'))
# len(unwatermarked)
# type(unwatermarked)

In [10]:
len(unwatermarked)

1000

In [183]:
def call_llm_recognize(model, prompt_dataset, watermarked_dataset, unwatermarked_dataset, model_name, unwatermarked_indice, rank:bool=False,  
                       save: bool=False, path_rec:str="watermark_recognition.json", path_raw="watermark_recognition_raw.json", batch_size:int=1):
    def parse_output(ID, output:str, with_expl:bool):
        pass

    if os.path.exists(path_rec):
        record_rec = load_json_file(path_rec)
    else:
        record_rec = dict()
    
    chat_prompt = ChatPromptTemplate.from_template(rank_prompt_string) if rank else ChatPromptTemplate.from_template(simple_prompt_string)
    key = f"{model_name}_recognition_rank_{rank}"
    IDs = list(map(lambda s: str(s), list(range(epoch))))
    shuffle(IDs)
    IDs_loaded = record_rec.keys()
    IDs = list(set(IDs) - set(IDs_loaded))
    batch_inputs = []
    final_outputs = []
    batch_count = 0
    batch_ID = []
    test_count = 0
    for ID in tqdm(IDs, desc="Processing"):
        prompt = prompt_dataset[ID]
        unwatermarked_sent = unwatermarked_dataset[ID]
        watermarked_sent = watermarked_dataset[ID]
        unwatermarked_index = unwatermarked_indice[int(ID)] # 0 means A is unwatermarked, 1 means B is unwatermarked
        _input = chat_prompt.format_messages(prompt = prompt, answer_a = unwatermarked_sent, answer_b = watermarked_sent) if unwatermarked_index \
            else chat_prompt.format_messages(prompt = prompt, answer_a = watermarked_sent, answer_b = unwatermarked_sent)
        batch_inputs.append(_input)
        batch_count += 1
        batch_ID.append(ID)
        if batch_count == batch_size:
            batch_count = 0
            _inputs = [[msg.content for msg in input_batch] for input_batch in batch_inputs]
            # pprint(_inputs)
            _outputs = [o1.content for o1 in model.batch(_inputs)]
            # print(_outputs)
            final_outputs.extend({ID:_output} for ID, _output in zip(batch_ID, _outputs))
            batch_inputs = []
            batch_ID = []
        test_count += 1       

    return final_outputs
            
gpt35_name = 'gpt-3.5-turbo-1106'
gpt4_name = 'gpt-4-1106-preview'
temperature = 0.0
# openai_api_key = os.getenv("OPENAI_API_KEY")
openai_api_key = GET_OPENAI_API_KEY()
gpt35 = ChatOpenAI(model_name=gpt35_name, temperature=temperature,
                   openai_api_key=openai_api_key, request_timeout=120)
gpt4 = ChatOpenAI(model_name=gpt4_name, temperature=temperature,
                   openai_api_key=openai_api_key, request_timeout=120)
max_attempts = 10
attempt = 0
while attempt < max_attempts:
    try:
        raw_response_result = call_llm_recognize(gpt35, decoded_text_inputs, output_text_list, output_text_normal_list, 'gpt-35', unwatermarked_indice= unwatermarked, rank=True, save=False, batch_size = 50)
        break
    except:
        attempt += 1
        time.sleep(2)    
else:
    # This part runs if the loop completes without breaking - meaning all attempts failed
    print(f'Failed to make the API call after {max_attempts} attempts.')


Processing:   5%|███████▎                                                                                                                                             | 49/1000 [00:01<00:24, 38.58it/s]


KeyboardInterrupt: 

In [171]:
pprint(raw_response_result)

[{'201': '```json\n'
         '{\n'
         '  "LLM A’s Answer": {\n'
         '    "Relevance to the prompt": 5,\n'
         '    "Depth of detail": 4,\n'
         '    "Clarity of writing": 5,\n'
         '    "Coherence and logical flow": 5,\n'
         '    "Originality and insight": 3,\n'
         '    "Use of specific examples": 3,\n'
         '    "Accuracy of information": 4\n'
         '  },\n'
         '  "LLM B\'s Answer": {\n'
         '    "Relevance to the prompt": 5,\n'
         '    "Depth of detail": 4,\n'
         '    "Clarity of writing": 5,\n'
         '    "Coherence and logical flow": 4,\n'
         '    "Originality and insight": 4,\n'
         '    "Use of specific examples": 4,\n'
         '    "Accuracy of information": 3\n'
         '  },\n'
         '  "Summary": {\n'
         '    "LLM A’s Answer": "Assistant A\'s response is directly relevant '
         'to the prompt, discussing the impact of the eurozone economy on '
         'shipping carriers, specif

In [143]:
# print(len(raw_response_result))
# assert len(raw_response_result) == 9, "Output size mismatch input size!"
# pprint(result[0])

def simple_response_parse(response):    
    updated_pattern = r"([fF]inal [vV]erdict:.*$)"
    final_choice_pattern = r"\[\[(.*?)\]\]"
    verdict_pattern = r'\[\[(A|B|C)\]\]'
    # Use the updated regex pattern to split the response and capture the final verdict including subsequent text
    updated_parts = re.split(updated_pattern, response, flags=re.DOTALL)
    # Organize the result for return with the updated pattern
    # print(updated_parts)
    # print(updated_parts[0])
    # print(updated_parts[1])
    updated_result_without_verdict = updated_parts[0].strip() if len(updated_parts) > 1 else ""
    updated_final_verdict = updated_parts[1].strip() if len(updated_parts) > 2 else ""
    updated_result_without_verdict, updated_final_verdict
    
    # Further use the regex pattern to find and extract the final choice
    final_choice_match = re.search(final_choice_pattern, updated_final_verdict)
    final_choice = final_choice_match.group(1) if final_choice_match else ""
    if final_choice:
        updated_result_without_verdict = updated_result_without_verdict
        status = 0
    else:
        verdict_match = re.search(verdict_pattern, response)
        final_choice = verdict_match.group(1) if verdict_match else None
        if final_choice:
            updated_result_without_verdict = updated_result_without_verdict
            status = 0
        else:
            updated_result_without_verdict = response
            status = 1
    
    
    return {"reason": updated_result_without_verdict, "choice": final_choice}, status

# print(simple_response_parse(raw_response_result[6]))
    
gpt_4_simple_result_verdict = []
gpt_4_simple_error_parsing = []
for index in range(len(raw_response_result)):
    parsed_result, status = simple_response_parse(raw_response_result[index])
    if status:
        gpt_4_simple_error_parsing.append(index)
    gpt_4_simple_result_verdict.append(parsed_result)

TypeError: expected string or bytes-like object, got 'dict'

In [184]:
# print(len(raw_response_result))
# print(len(unwatermarked))
assert len(raw_response_result) == epoch, f"Output size mismatch input size! Input size is {epoch}, Output size is {len(raw_response_result)}"
def rank_response_parser(raw_response_result, unwatermarked, model_name):
    parsed_response_list = []
    error_indice = []
    separated_content_list = dict()
    for i in range(len(raw_response_result)):
        unwatermarked_index = unwatermarked[i]
        ID = str([id for id in raw_response_result[i].keys()][0])
        json_content = raw_response_result[i][ID].strip('```json\n').rstrip('```')
        try:
            parsed_response = json.loads(json_content)
            parsed_response_list.append(parsed_response)
            rank_A = list(parsed_response['LLM A’s Answer'].values())
            rank_B = list(parsed_response['LLM A’s Answer'].values())
            summary = parsed_response['Summary']
            verdict = parsed_response['Verdict']
            separated_content_list[ID] = {
                "unwatermarked_index": unwatermarked_index,
                f"{model_name}_ranking": {
                  "rank_A": rank_A,
                  "rank_B": rank_B,
                  "reasons": summary,
                  "choice": verdict
                }
            }
        except (json.JSONDecodeError, AttributeError, KeyError) as e:  # Referencing JSONDecodeError through the json module
            error_indice.append(i)
            separated_content_list[ID] = {
                "unwatermarked_index": None,
                f"{model_name}_ranking": {
                  "rank_A": None,
                  "rank_B": None,
                  "reasons": None,
                  "choice": None
                }
            }
            print(f"Caught an exception: {type(e).__name__} - {str(e)}")
    error_indice_dict = {f"{model_name}_ranking": error_indice}
    return error_indice_dict, parsed_response_list, separated_content_list

A,B,C = rank_response_parser(raw_response_result, unwatermarked, 'gpt_4')

Caught an exception: JSONDecodeError - Extra data: line 27 column 1 (char 1682)
Caught an exception: JSONDecodeError - Extra data: line 26 column 1 (char 1292)
Caught an exception: KeyError - 'Summary'
Caught an exception: KeyError - 'Summary'
Caught an exception: JSONDecodeError - Invalid control character at: line 20 column 741 (char 1252)
Caught an exception: KeyError - 'Summary'
Caught an exception: JSONDecodeError - Extra data: line 26 column 1 (char 1226)
Caught an exception: KeyError - 'Summary'
Caught an exception: KeyError - 'Summary'
Caught an exception: KeyError - 'Summary'
Caught an exception: JSONDecodeError - Expecting ',' delimiter: line 22 column 286 (char 1462)
Caught an exception: KeyError - 'Summary'
Caught an exception: KeyError - 'Summary'
Caught an exception: KeyError - 'Summary'
Caught an exception: JSONDecodeError - Extra data: line 26 column 1 (char 1184)
Caught an exception: JSONDecodeError - Extra data: line 26 column 1 (char 1266)
Caught an exception: KeyErr

In [187]:
file_response_name = 'parsed_response.json'
file_separated_response_name = 'separated_content.json'
file_error_indice = "error_indice.json"

with open(file_error_indice, 'w') as file:
    json.dump(A, file, indent=4)
# with open(file_response_name, 'w') as file:
#     json.dump(B, file, indent=4)
# with open(file_separated_response_name, 'w') as file:
#     json.dump(C, file, indent=4)

In [168]:
# for key, content in C.items():
#     # print(content)
#     content['gpt_4_ranking']['rank_A'] = list(content['gpt_4_ranking']['rank_A']) if content['gpt_4_ranking']['rank_A'] else None
#     content['gpt_4_ranking']['rank_B'] = list(content['gpt_4_ranking']['rank_B']) if content['gpt_4_ranking']['rank_B'] else None

Depracated post-processing functions

In [242]:
# pprint(raw_response_result[0])

# Regex pattern to extract ratings, reasons, and final verdict
ratings_pattern = r"\[LLM (A|B)’s Answer\]\n(.*?)\n\n"
verdict_pattern = r'Verdict:\n"(\[\[.*?\]\]: \[.*?\])"'

# Find all ratings and reasons for A and B
ratings_matches = re.findall(ratings_pattern, raw_response_result[0], flags=re.DOTALL)
print(ratings_matches)
# Find final verdict
verdict_match = re.search(verdict_pattern, raw_response_result[0])

# Extract and organize ratings, reasons, and final verdict
ratings = {}
reasons = {}
for match in ratings_matches:
    assistant, details = match
    ratings[assistant], reason_list = [], []
    for line in details.strip().split('\n'):
        if line.startswith(assistant):
            continue  # Skip lines that are just headings
        elif line[1:].startswith('.'):
            # This is a rating line
            rating = line.split(':')[-1].strip()
            ratings[assistant].append(int(rating))
        else:
            # This is a reason line
            reason_list.append(line.strip())
    reasons[assistant] = ' '.join(reason_list)

final_verdict = verdict_match.group(1) if verdict_match else ""

ratings, reasons, final_verdict

[('A', '1. Relevance to the prompt: 5\nThe response is directly relevant to the prompt, discussing the IBM cluster and its components.'), ('B', '1. Relevance to the prompt: 4\nThe response is relevant but does not mention the Opteron processor, which is a key component of the prompt.')]


({'A': [5], 'B': [4]},
 {'A': 'The response is directly relevant to the prompt, discussing the IBM cluster and its components.',
  'B': 'The response is relevant but does not mention the Opteron processor, which is a key component of the prompt.'},
 '[[A]]: [5, 4, 5, 5, 3, 4, 5]')

In [292]:
# print(len(raw_response_result))

def rank_response_parser(response):
    assistant_a_match = re.search("(Assistant A:\n|\\*\\*LLM B’s Answer\\*\\*\n|\\[LLM A’s Answer\\]\n)(.*?)(Assistant B:|LLM B’s Answer|\\[LLM B’s Answer\\]\n|Verdict:)", response, flags=re.DOTALL)
    assistant_b_match = re.search("(Assistant B:\n|\\*\\*LLM B’s Answer\\*\\*\n|\\[LLM B’s Answer\\]\n)(.*?)(Verdict:)", response, flags=re.DOTALL)
    verdict_match = re.search("(Verdict:.*)", response, flags=re.DOTALL)

    # Extract the matched groups
    assistant_a_section = assistant_a_match.group(2) if assistant_a_match else "Not found"
    assistant_b_section = assistant_b_match.group(2) if assistant_b_match else "Not found"
    verdict_section = verdict_match.group(1) if verdict_match else "Not found"
    status = 1 if any(var == 'Not found' for var in [assistant_a_section, assistant_b_section, verdict_section]) else 0
    if status:
        return {"rank_A":None, "rank_B":None, "choice":response}, status
    
    # pprint(assistant_a_section)
    # pprint(assistant_b_section)
    # pprint(verdict_section)


    # pprint(assistant_b_match.group(2))
    pattern = r'^\d+\..*?$'
    try:
        a_matches = re.findall(pattern, assistant_a_match.group(2), flags=re.MULTILINE) if assistant_a_match.group(2) else "Not found"
        b_matches = re.findall(pattern, assistant_b_match.group(2), flags=re.MULTILINE) if assistant_b_match.group(2) else "Not found"
        # pprint(b_matches)
    
        a_scores = [int(re.search(r'\d+$', sentence).group()) for sentence in a_matches]
        b_scores = [int(re.search(r'\d+$', sentence).group()) for sentence in b_matches]
    
        verdict_choices = [re.search(r'\[\[([A-C])\]\]', verdict_section).group(1)]
    except AttributeError:
         return {"rank_A":None, "rank_B":None, "choice":response}, 1
        
    # print(verdict_choices)
    # pprint(a_scores)
    # pprint(b_scores)
    # print("*"*100)
    status = 1 if any(var is None for var in [a_scores, b_scores, verdict_choices]) else 0
    return {"rank_A":a_scores, "rank_B":b_scores, "choice":verdict_choices[0]}, 0
    
# pprint(raw_response_result[1])
# rank_response_parser(raw_response_result[1])
    
result_list = []
error_parsing = []
for index in range(len(raw_response_result)):
    parsed_result, status = rank_response_parser(raw_response_result[index])
    result_list.append(parsed_result)
    # print(status)
    if status:
        error_parsing.append(index)
print(len(error_parsing))

for i in error_parsing:
    pprint(raw_response_result[i])
    print("\n"+ "=" * 100 +'\n')

709
('Based on the provided text completions, I will now evaluate each response '
 'according to the criteria.\n'
 '\n'
 '**Relevance to the prompt:**\n'
 '- LLM A: 1\n'
 '- LLM B: 1\n'
 '\n'
 'Both responses incorrectly convert the original figure of Rs 58.19 crore '
 'into Rs 58.19 billion, which is a significant error and not relevant to the '
 "prompt's information.\n"
 '\n'
 '**Depth of detail:**\n'
 '- LLM A: 2\n'
 '- LLM B: 2\n'
 '\n'
 'Both responses attempt to provide additional context regarding the revenue '
 'figures, but due to the inaccuracy in the conversion of the currency, the '
 'depth of detail is compromised.\n'
 '\n'
 '**Clarity of writing:**\n'
 '- LLM A: 3\n'
 '- LLM B: 3\n'
 '\n'
 'Both responses are written in clear language, but the clarity is '
 'overshadowed by the critical error in the financial figures.\n'
 '\n'
 '**Coherence and logical flow:**\n'
 '- LLM A: 3\n'
 '- LLM B: 3\n'
 '\n'
 'Each response maintains a coherent and logical flow in the informatio

In [269]:
# print(len(raw_response_result))
# assert len(raw_response_result) == 9, "Output size mismatch input size!"
# pprint(result[0])

def simple_response_parse(response):    
    updated_pattern = r"([fF]inal [vV]erdict:.*$)"
    final_choice_pattern = r"\[\[(.*?)\]\]"
    verdict_pattern = r'\[\[(A|B|C)\]\]'
    # Use the updated regex pattern to split the response and capture the final verdict including subsequent text
    updated_parts = re.split(updated_pattern, response, flags=re.DOTALL)
    # Organize the result for return with the updated pattern
    # print(updated_parts)
    # print(updated_parts[0])
    # print(updated_parts[1])
    updated_result_without_verdict = updated_parts[0].strip() if len(updated_parts) > 1 else ""
    updated_final_verdict = updated_parts[1].strip() if len(updated_parts) > 2 else ""
    updated_result_without_verdict, updated_final_verdict
    
    # Further use the regex pattern to find and extract the final choice
    final_choice_match = re.search(final_choice_pattern, updated_final_verdict)
    final_choice = final_choice_match.group(1) if final_choice_match else ""
    if final_choice:
        updated_result_without_verdict = updated_result_without_verdict
        status = 0
    else:
        verdict_match = re.search(verdict_pattern, response)
        final_choice = verdict_match.group(1) if verdict_match else None
        if final_choice:
            updated_result_without_verdict = updated_result_without_verdict
            status = 0
        else:
            updated_result_without_verdict = response
            status = 1
    
    
    return {"reason": updated_result_without_verdict, "choice": final_choice}, status

# print(simple_response_parse(raw_response_result[6]))
    
gpt_4_simple_result_verdict = []
gpt_4_simple_error_parsing = []
for index in range(len(raw_response_result)):
    parsed_result, status = simple_response_parse(raw_response_result[index])
    if status:
        gpt_4_simple_error_parsing.append(index)
    gpt_4_simple_result_verdict.append(parsed_result)

In [268]:
# Regular expression pattern to match and extract the final choice within double brackets
print(len(error_parsing))
remain_list = []
for i in error_parsing:
    remain_list.append(raw_response_result[i])
print(remain_list)

55
["Comparing the two responses, LLM A provides a more detailed continuation of the prompt. It adds information about the type of participants the event is seeking and includes a call to action for those who are passionate about building for the social web. This continuation is more in line with the promotional nature of the prompt, as it encourages participation and outlines the target audience for the event.\n\nLLM B, on the other hand, offers a very brief completion, only providing a location for the event. While this is a relevant piece of information, it does not expand on the prompt in a meaningful way or engage the reader as effectively as LLM A's response.\n\nBased on the criteria of relevance, engagement, and the ability to provide a meaningful continuation of the prompt, LLM A's answer is superior.\n\n[[A]]", 'Comparing the two responses, both LLM A and LLM B provide a continuation that is relevant to the prompt. LLM A elaborates on the previous difficulty of uploading and d